In [52]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import pandas as pd 
from pandas_datareader import data
import requests
import re
import urllib
import io
import matplotlib.pyplot as plt
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()


DataTransformerRegistry.enable('default')

In [53]:
fdf=pd.DataFrame
for nodes in ['3','5']:
    for threads in ['1','2','4','8','16','64','128','256']:
#    for threads in ['1']:
        url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
        #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-5nodes-1writer-BP25G-1/res_thr1.txt'
        s=requests.get(url)


        buf=[]
        for line in s.text.splitlines():
            #rint(line)
            if re.match("^[0-9]", line):
                buf.append(line)

        df = pd.DataFrame([x.split(',') for x in buf])
        df['Nodes'] = nodes
        if fdf.empty:
           fdf=df
        else: 
           fdf=fdf.append(df,ignore_index = False)



In [24]:
fdf

0    1        2          3         4         5        6       7  \
0        1    1   118.76    3873.12   1776.39   1856.22   240.51   17.32   
1        2    1   145.05    3772.36   1712.62   1769.64   290.10   17.32   
2        3    1   142.00    3993.98   1813.99   1895.99   284.00   16.41   
3        4    1   127.00    3548.95   1608.98   1685.98   254.00   19.29   
4        5    1   128.00    3819.05   1761.02   1802.02   256.00   15.27   
...    ...  ...      ...        ...       ...       ...      ...     ...   
1795  1796  256  4855.96  137750.87  62819.48  65218.46  9712.92  155.80   
1796  1797  256  3807.03  110848.78  50694.36  52562.37  7592.05  227.40   
1797  1798  256  4234.98  117966.46  53738.76  55735.75  8491.96  211.60   
1798  1799  256  4122.07  119134.92  54241.88  56646.91  8246.13  186.54   
1799  1800  256  4094.98  115423.54  52634.79  54598.78  8189.97  235.74   

          8     9 Nodes  
0      0.00  0.00     3  
1      0.00  0.00     3  
2      0.00  0.00     3  
3      0.00  0.00     3  
4      1.00  0.00     3  
...     ...   ...   ...  
1795  22.00  0.00     5  
1796  20.00  0.00     5  
1797  11.00  0.00     5  
1798  23.00  0.00     5  
1799  23.00  0.00     5  

[28800 rows x 11 columns]

In [54]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [196]:
fdf[fdf.threads == '8']

sec threads      tps      read     write     other       v1     v2  \
0        1       8  1092.06  29906.93  13615.84  14084.01  2207.08  17.32   
1        2       8  1233.08  34279.20  15624.00  16189.04  2466.16  15.00   
2        3       8  1207.00  33585.93  15361.97  15808.97  2414.99  13.70   
3        4       8  1192.99  33815.84  15378.93  16051.92  2384.99  17.63   
4        5       8  1236.99  34387.72  15664.87  16248.87  2473.98  15.00   
...    ...     ...      ...       ...       ...       ...      ...    ...   
1795  1796       8  1177.00  33029.10  15105.05  15570.05  2354.01  14.73   
1796  1797       8  1235.99  34388.62  15676.82  16239.82  2471.97  14.21   
1797  1798       8  1150.00  33554.07  15320.03  15934.03  2300.00  15.27   
1798  1799       8  1174.00  33552.00  15377.00  15826.00  2349.00  13.95   
1799  1800       8  1201.99  32551.66  14874.84  15275.84  2400.97  13.95   

         v3    v4  
0      4.99  0.00  
1      2.00  0.00  
2     10.00  0.00  
3      2.00  0.00  
4      9.00  0.00  
...     ...   ...  
1795   7.00  0.00  
1796   3.00  0.00  
1797  11.00  0.00  
1798   5.00  0.00  
1799   4.00  0.00  

[1800 rows x 10 columns]

In [329]:
fdf.query('nodes == "3" and sec>900')

sec  threads      tps      read     write     other       v1      v2  \
900    901.0        1    93.00   2847.01   1300.00   1361.01   186.00   22.69   
901    902.0        1   112.00   2990.99   1357.99   1408.99   224.00   21.11   
902    903.0        1   109.00   3115.00   1429.00   1468.00   218.00   20.00   
903    904.0        1    91.00   2838.00   1317.00   1339.00   182.00   22.28   
904    905.0        1    86.00   2482.01   1141.00   1169.00   172.00   26.20   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0      256  1692.00  49137.97  22361.99  23391.98  3384.00  816.63   
1796  1797.0      256  1541.00  44455.98  20301.99  21071.99  3082.00  861.95   
1797  1798.0      256  1374.00  40558.89  18462.95  19347.95  2747.99  861.95   
1798  1799.0      256  1212.00  33145.10  15047.05  15674.05  2424.01  893.56   
1799  1800.0      256  1715.01  48300.25  22030.12  22840.12  3430.02  909.80   

         v3    v4 nodes  
900    1.00  0.00     3  
901    0.00  0.00     3  
902    0.00  0.00     3  
903    0.00  0.00     3  
904    0.00  0.00     3  
...     ...   ...   ...  
1795  10.00  0.00     3  
1796   7.00  0.00     3  
1797   2.00  0.00     3  
1798   5.00  0.00     3  
1799   9.00  0.00     3  

[7200 rows x 11 columns]

In [5]:
fdf

0    1        2          3         4         5         6       7  \
0        1    1    34.92    1107.58    504.90    529.84     72.84   52.89   
1        2    1    46.02    1354.66    613.30    649.32     92.04   62.19   
2        3    1    44.00    1287.02    580.01    619.01     88.00   56.84   
3        4    1    47.00    1373.00    630.00    649.00     94.00   41.10   
4        5    1    49.00    1247.00    574.00    575.00     98.00   47.47   
...    ...  ...      ...        ...       ...       ...       ...     ...   
1795  1796  256  2640.92   79455.45  36291.83  37815.78   5347.83  719.92   
1796  1797  256  2822.04   75699.96  34496.44  35619.45   5584.07  746.32   
1797  1798  256  3730.96  103390.90  47196.50  48723.48   7470.92  646.19   
1798  1799  256  5410.74  153955.97  70205.82  72941.65  10808.50   53.85   
1799  1800  256  2505.90   75962.19  34787.13  36099.17   5075.90  746.32   

          8     9 Nodes  
0      0.00  0.00     3  
1      0.00  0.00     3  
2      0.00  0.00     3  
3      1.00  0.00     3  
4      1.00  0.00     3  
...     ...   ...   ...  
1795   8.00  0.00     5  
1796  16.00  0.00     5  
1797  18.00  0.00     5  
1798  24.96  0.00     5  
1799  10.02  0.00     5  

[28800 rows x 11 columns]

In [55]:


stripplot =  alt.Chart(fdf.query('nodes == "3"'), width=100,title='3nodes, threads 1-256').mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False, title='Threads'),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q',title="Throughput, tps"),
    order='threads:O',
    color=alt.Color('threads:N', legend=None),
    column=alt.Column(
        'threads:N',
        header=alt.Header(
            labelAngle=0,
            titleOrient='top',
            labelOrient='bottom',
            labelAlign='center',
            labelPadding=10,
        ),
    ),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
)

stripplot


alt.Chart(...)

In [61]:
import altair as alt
from vega_datasets import data
alt.data_transformers.disable_max_rows()
from altair.expr import datum

stripplot =  alt.Chart(fdf.query('sec>900'), width=100,title='3 vs 5 nodes, threads 1-256').mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('tps:Q', title="Throughput, tps"),
    order='threads:O',
    color='nodes:N',
    facet=alt.Facet('threads:O', columns=5,align="none"),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).resolve_scale(y='independent').interactive().add_selection(alt.selection_single(empty='all', fields=['nodes']))

#chart = alt.hconcat()
#for threads in ['1','2','4','8','16','64','128','256']:
#    chart |= stripplot.transform_filter(datum.threads == threads)
#chart

stripplot

alt.Chart(...)

In [59]:


alt.Chart(fdf.query('nodes == "3" and sec>900 and threads=="64"'),width=800,title="64 threads").mark_line().encode(
    x='sec',
    y='tps'
)



alt.Chart(...)

In [30]:
fdf=pd.DataFrame
for nodes in ['3','5']:
#    for threads in ['1','2','4','8','16','64','128','256']:
#    for threads in ['1']:
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-1/res_thr'+threads+'.txt'
    url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-'+nodes+'nodes-1writer-BP25G-txrate3100-1/res_thr64.txt'
    #url='https://raw.githubusercontent.com/Percona-Lab-results/PXC-8-March2020/master/res-tpcc-GR-5nodes-1writer-BP25G-1/res_thr1.txt'
    s=requests.get(url)


    buf=[]
    for line in s.text.splitlines():
        #rint(line)
        if re.match("^[0-9]", line):
            buf.append(line)

    df = pd.DataFrame([x.split(',') for x in buf])
    df['Nodes'] = nodes
    if fdf.empty:
       fdf=df
    else: 
       fdf=fdf.append(df,ignore_index = False)

In [36]:
fdf.columns =['sec','threads','tps','read','write','other','v1','rt','v3','v4','nodes']
fdf['tps']=fdf['tps'].astype(float)
fdf['sec']=fdf['sec'].astype(float)
fdf['rt']=fdf['rt'].astype(float)
fdf['threads']=fdf['threads'].astype(int)

In [33]:
fdf

sec  threads      tps      read     write     other       v1      rt  \
0        1.0       64  3023.76  84691.24  38627.06  39872.91  6191.27   23.95   
1        2.0       64  3070.13  87747.71  40053.69  41543.76  6150.26   24.38   
2        3.0       64  3236.00  91827.97  42024.99  43319.99  6483.00   24.83   
3        4.0       64  3140.98  88537.38  40427.72  41828.71  6280.96   26.68   
4        5.0       64  3096.04  87770.03  40091.47  41488.49  6190.07   24.83   
...      ...      ...      ...       ...       ...       ...      ...     ...   
1795  1796.0       64  2999.99  84772.63  38729.83  40013.83  6028.97  179.94   
1796  1797.0       64  3107.95  86374.48  39354.31  40813.28  6206.89   24.83   
1797  1798.0       64  3104.05  90018.56  41106.71  42708.74  6203.11   23.10   
1798  1799.0       64  2992.93  85628.05  39033.11  40611.07  5983.86   24.38   
1799  1800.0       64  3154.62  90155.26  41107.10  42738.91  6309.25   23.95   

         v3    v4 nodes  
0      9.98  0.00     3  
1     13.00  0.00     3  
2     11.00  0.00     3  
3     11.00  0.00     3  
4     21.00  0.00     3  
...     ...   ...   ...  
1795  14.00  0.00     5  
1796  17.00  0.00     5  
1797   7.00  0.00     5  
1798   8.00  0.00     5  
1799  11.00  0.00     5  

[3600 rows x 11 columns]

In [46]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('rt:Q', title="95% response time, ms"),
    color='nodes:N'
)

alt.Chart(...)

In [49]:
alt.Chart(fdf,width=800,title="64 threads, 3100 tps incoming rate").mark_point(size=5).encode(
    x='sec',
    y=alt.Y('tps:Q', title="Throughput, tps"),
    color='nodes:N'
)

alt.Chart(...)